In [1]:

import pandas as pd
import numpy as np

from sklearn.datasets import make_moons
from sklearn.cluster import KMeans
from sklearn.cluster import DBSCAN
from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import train_test_split
from sklearn.pipeline import Pipeline
from sklearn.preprocessing import LabelEncoder, OneHotEncoder, StandardScaler
from sklearn.compose import ColumnTransformer
from sklearn.impute import SimpleImputer
from sklearn.metrics import silhouette_score
from sklearn.metrics import (
    accuracy_score,
    f1_score,
    ConfusionMatrixDisplay,
    RocCurveDisplay)
import hdbscan

import matplotlib.pyplot as plt
import cartopy.crs as ccrs
import cartopy.feature as cfeature
import plotly.express as px
import plotly.graph_objects as go
import plotly.io as pio
import seaborn as sns
import geopandas as gpd

import warnings
warnings.filterwarnings('ignore')

from sklearn.decomposition import PCA
import os

os.environ["OMP_NUM_THREADS"] = "1"

In [2]:
df_avr = pd.read_csv( 'src/uber-raw-data-apr14.csv')
df_mai = pd.read_csv( 'src/uber-raw-data-may14.csv') 
df_juin= pd.read_csv( 'src/uber-raw-data-jun14.csv')
df_juil = pd.read_csv( 'src/uber-raw-data-jul14.csv')
df_aou = pd.read_csv( 'src/uber-raw-data-aug14.csv')
df_sep = pd.read_csv( 'src/uber-raw-data-sep14.csv')

In [3]:
# Regroupement des différents mois.
data= pd.concat([df_avr, df_mai, df_juin, df_juil, df_aou, df_sep], ignore_index=True)

In [4]:
data.describe(include="all")

Date/Time           Lat           Lon     Base
count             4534327  4.534327e+06  4.534327e+06  4534327
unique             260093           NaN           NaN        5
top     4/7/2014 20:21:00           NaN           NaN   B02617
freq                   97           NaN           NaN  1458853
mean                  NaN  4.073926e+01 -7.397302e+01      NaN
std                   NaN  3.994991e-02  5.726670e-02      NaN
min                   NaN  3.965690e+01 -7.492900e+01      NaN
25%                   NaN  4.072110e+01 -7.399650e+01      NaN
50%                   NaN  4.074220e+01 -7.398340e+01      NaN
75%                   NaN  4.076100e+01 -7.396530e+01      NaN
max                   NaN  4.211660e+01 -7.206660e+01      NaN

In [5]:
# Définir les limites pour Manhattan et ses environs
lat_min = 40.5
lat_max = 40.88  # Limite supérieure pour Manhattan
lon_min = -74.2  # Limite ouest pour Manhattan
lon_max = -73.85  # Limite est pour Manhattan

# Filtrer les données pour ne garder que les coordonnées de Manhattan
manhattan_data = data[(data['Lat'] >= lat_min) & (data['Lat'] <= lat_max) &
                      (data['Lon'] >= lon_min) & (data['Lon'] <= lon_max)]


In [6]:
# Création de l'échantillon
manhattan_data = manhattan_data.sample(frac=0.01, random_state=0)
display(manhattan_data.head())
display(manhattan_data.shape)

Date/Time      Lat      Lon    Base
2361296  7/22/2014 22:49:00  40.7084 -74.0007  B02617
3489658  8/26/2014 16:10:00  40.8001 -73.9692  B02764
1623002  6/23/2014 10:47:00  40.7723 -73.9467  B02617
3262418  8/29/2014 19:16:00  40.7927 -73.9234  B02617
1375455  6/15/2014 20:18:00  40.7226 -73.9593  B02598

(43387, 4)

In [7]:
# Création des données de temps à partir du Date/Time
manhattan_data['Date/Time'] = pd.to_datetime(manhattan_data['Date/Time'])
manhattan_data['hour']=manhattan_data['Date/Time'].dt.hour
manhattan_data['month'] = manhattan_data['Date/Time'].dt.month
manhattan_data['dayofweek'] = manhattan_data['Date/Time'].dt.dayofweek
manhattan_data['day'] = manhattan_data['Date/Time'].dt.day
manhattan_data.head()

Date/Time      Lat      Lon    Base  hour  month  dayofweek  \
2361296 2014-07-22 22:49:00  40.7084 -74.0007  B02617    22      7          1   
3489658 2014-08-26 16:10:00  40.8001 -73.9692  B02764    16      8          1   
1623002 2014-06-23 10:47:00  40.7723 -73.9467  B02617    10      6          0   
3262418 2014-08-29 19:16:00  40.7927 -73.9234  B02617    19      8          4   
1375455 2014-06-15 20:18:00  40.7226 -73.9593  B02598    20      6          6   

         day  
2361296   22  
3489658   26  
1623002   23  
3262418   29  
1375455   15

In [8]:
# Groupe les données par heure et calcule la somme des éléments pour chaque heure
df_grouped = manhattan_data.groupby('hour').size().reset_index(name='count')

# Crée un graphique en utilisant Plotly Express
fig = px.scatter(df_grouped, x='hour', y='count', title='Somme des courses par heure',
                 labels={'hour': 'Heure', 'count': 'Somme des courses'})

# Affiche le graphique
fig.show()

In [9]:
# Groupe les données par heure et calcule la somme des éléments pour chaque heure
df_grouped = manhattan_data.groupby('month').size().reset_index(name='count')

# Crée un graphique en utilisant Plotly Express
fig = px.scatter(df_grouped, x='month', y='count', title='Somme des courses par mois',
                 labels={'month': 'Mois', 'count': 'Somme des courses'})

# Affiche le graphique
fig.show()

On remarque que plus on avance dans l'année (peut être lié à l'approche de l'hiver), le nombre de courses augmente avec un gros pique en septembre.

In [10]:
# Groupe les données par heure et calcule la somme des éléments pour chaque heure
df_grouped = manhattan_data.groupby('dayofweek').size().reset_index(name='count')

# Crée un graphique en utilisant Plotly Express
fig = px.scatter(df_grouped, x='dayofweek', y='count', title='Somme des courses par jour de la semaine',
                 labels={'dayofweek': 'Jour de la semaine', 'count': 'Somme des courses'})

# Met à jour les étiquettes de l'axe des x
fig.update_layout(xaxis={'type': 'category'})

# Affiche le graphique
fig.show()

Le jour ayant le plus de courses sur la semaine est donc le jeudi

In [11]:
# Crée un tableau vide de dimensions 24x7
p = np.empty(shape=(24, 7), dtype=int)

# Remplit le tableau avec le nombre d'éléments par heure et par jour de la semaine
for i in range(24):
    for j in range(7):
        p[i, j] = len(manhattan_data[(manhattan_data['hour'] == i) & (manhattan_data['dayofweek'] == j)])

# Crée un DataFrame à partir du tableau
df = pd.DataFrame(p)

# Crée une figure en utilisant Plotly
fig = go.Figure()

# Ajoute des traces à la figure pour chaque jour de la semaine
for j, day in enumerate(['Mon', 'Tue', 'Wed', 'Thu', 'Fri', 'Sat', 'Sun']):
    fig.add_trace(go.Scatter(x=np.arange(24), y=df[j], mode='lines', name=day))

# Ajoute des informations sur les axes et le titre
fig.update_layout(title='Nombre de courses par heure et par jour de la semaine',
                  xaxis_title='Heure',
                  yaxis_title='Nombre d\'éléments')

# Affiche la figure
fig.show()

Avec ce graphique, on peut remarqué différentes tendances. 
- Du lundi au jeudi, on a un premier pique entre 7 et 8h du matin (heure de départ au travail) puis un autre à 17h (départ du travail)
- Le vendredi connait les mêmes piques qu'en semaine, cependant il en a un autre à 22h ce qui nous laisse comprendre que les gens sortent.
- Le samedi va connaitre une hausse constante tout au long de la journée pour stagner entre 16 et 22h.
- Le dimanche a son plus gros pique à minuit ainsi qu'un autre à 16h.

In [12]:
fig = px.scatter_mapbox(manhattan_data, lat="Lat", lon="Lon",size_max=15, zoom=8, width=800, height=800, title="Ensemble des courses Uber")
fig.update_layout(mapbox_style="carto-positron")

fig.show()

## Silhouette & Elbow

In [13]:
# Sélection des données géographiques
df_test=manhattan_data[['Lat','Lon']]

In [14]:
# Calcul du score de silhouette moyen
sil = []
k = []

# Confirguer le kmeans
for i in range(2, 10):
    kmeans = KMeans(n_clusters=i, random_state=0, n_init='auto')
    kmeans.fit(df_test)
    sil.append(silhouette_score(df_test, kmeans.predict(df_test)))
    k.append(i)

# Créer un DataFrame
cluster_scores = pd.DataFrame(sil)
k_frame = pd.Series(k)

# Créer le graphique
fig = px.bar(data_frame=cluster_scores,
             x=k,
             y=cluster_scores.iloc[:, -1])

# Ajouter un titre et des étiquettes d'axes
fig.update_layout(
    yaxis_title="Score de Silhouette",
    xaxis_title="# de Clusters",
    title="Score de Silhouette par cluster")

fig.show()


In [15]:
# Instanciation de KMeans avec k=6 et initialisation avec k-means++
kmeans = KMeans(n_clusters=6, random_state=0)

# Adapter kmeans à notre ensemble de données
kmeans.fit(df_test)

# Créons une boucle qui va collecter la somme des carrés intra-cluster (WCSS) pour chaque valeur K
# Utilisons le paramètre .inertia_ pour obtenir la somme des carrés intra-cluster pour chaque valeur K
wcss = []
k = []
for i in range(1, 10):
    kmeans = KMeans(n_clusters=i, random_state=0, n_init='auto')
    kmeans.fit(df_test)
    wcss.append(kmeans.inertia_)
    k.append(i)

# Créer un DataFrame
wcss_frame = pd.DataFrame(wcss)
k_frame = pd.Series(k)

# Créer le graphique
fig = px.line(
    wcss_frame,
    x=k_frame,
    y=wcss_frame.iloc[:, -1]
)

# Ajouter un titre et des étiquettes d'axes
fig.update_layout(
    yaxis_title="Inertie",
    xaxis_title="# de Clusters",
    title="Inertie par cluster"
)

# Afficher le graphique
fig.show()

In [16]:
# Choix de n_clusters en fonction des résultats de Elbow et Silhouette
kmeans = KMeans(n_clusters=5, random_state=0)
kmeans.fit(df_test)

# Prédire les clusters pour chaque échantillon
df_test['cluster'] = kmeans.labels_

# Créer une carte interactive avec Plotly Express
fig = px.scatter_mapbox(df_test, lon='Lon', lat='Lat', color='cluster', mapbox_style="carto-positron", title='Clusters des données géographiques par Kmeans', size_max=15, zoom=8, width=800, height=800)

# Afficher la carte interactive
fig.show()

## DBSCAN

In [17]:
# Configuration du modèle DBSCAN
db = DBSCAN(eps=0.1, min_samples=20, metric="euclidean")
db.fit(df_test)
np.unique(db.labels_, return_counts=True)

(array([0, 1, 2, 3, 4], dtype=int64),
 array([19069, 16185,  2044,  5694,   395], dtype=int64))

In [18]:
# Création de la carte interactive des clusters DBSCAN avec Plotly Express
df_test['cluster'] = db.labels_
fig = px.scatter_mapbox(df_test[df_test.cluster != -1], lon='Lon', lat='Lat', color='cluster', mapbox_style="carto-positron", title='Clusters des données géographiques par DBSCAN',size_max=15, zoom=8, width=800, height=800)

# Afficher la carte interactive
fig.show()

### HDBSCAN

In [19]:
# Paramètres de HDBSCAN
min_cluster_size = 200
min_samples = None  # Par défaut, il utilise min_cluster_size pour déterminer min_samples

# Création de l'instance HDBSCAN
hdb = hdbscan.HDBSCAN(min_cluster_size=min_cluster_size, min_samples=min_samples, metric="manhattan")

# Entraînement du modèle HDBSCAN
hdb.fit(df_test)

# Affichage des étiquettes de cluster et de leur compte
display(np.unique(hdb.labels_, return_counts=True))

(array([-1,  0,  1,  2,  3,  4,  5], dtype=int64),
 array([ 1199,   395,  5694, 16185, 19069,   453,   392], dtype=int64))

In [20]:
# Convertir les étiquettes de cluster en int64
cluster_labels = hdb.labels_.astype('int64')

# Ajouter les labels de cluster à votre DataFrame en utilisant .loc
df_test.loc[:, 'cluster'] = cluster_labels

# Filtrer les données pour ne conserver que les points assignés à un cluster
data_geo_assigned = df_test[df_test['cluster'] != -1]

# Définir le centre de la carte et le niveau de zoom pour afficher toutes les données
center_longitude = data_geo_assigned['Lon'].mean()
center_latitude = data_geo_assigned['Lat'].mean()
zoom_level = 8

# Spécifier une palette de couleurs qualitative avec plus de variations
colorscale = px.colors.qualitative.Dark24

# Créer une carte interactive avec Plotly Express en spécifiant le centre et le zoom
fig_all_hdb = px.scatter_mapbox(df_test, lon='Lon', lat='Lat', color='cluster', 
                                mapbox_style="carto-positron", title='Clusters des zones de transactions par HDBSCAN',
                                center=dict(lon=center_longitude, lat=center_latitude), zoom=zoom_level,
                                color_continuous_scale=colorscale,size_max=15, width=800, height=800)

# Afficher la carte interactive
fig_all_hdb.show()

Suite aux différentes modèles utilisés, on remarque que les résultats sont similaires. On a cependant moins d'outliers avec HDBSCAN que DBSCAN

### HOT SPOT

In [21]:
def cluster_day_hour(dataset, day, hour):
  # Sélectionne les données pour le jour et l'heure spécifiés dans le dataset
  df = dataset.loc[(dataset['hour'] == hour) & (dataset['dayofweek'] == day)]
  
  # Sélectionne seulement les colonnes 'Lat' et 'Lon' du dataframe
  df = df[['Lat', 'Lon']]
  
  # Standardisation des données pour les mettre à la même échelle
  scaler = StandardScaler()
  df_s = scaler.fit_transform(df)
  
  # Crée une instance de l'algorithme de clustering KMeans avec 4 clusters, initialisation 'k-means++' et un générateur de nombres aléatoires avec seed 42
  kmeans = KMeans(n_clusters=4, init='k-means++', random_state=42)
  
  # Prédit les clusters pour chaque point de données et ajoute cette information à la dataframe
  df['clusterkmeans'] = kmeans.fit_predict(df_s)
  
  # Retourne la dataframe avec les clusters assignés et les centres de clusters déstandardisés
  center = scaler.inverse_transform(kmeans.cluster_centers_)
  
  return df, center

In [22]:
# Appelle la fonction cluster_day_hour avec les données manhattan_data, le jour 6 et l'heure 0
df_sat_0, center = cluster_day_hour(manhattan_data, 6, 0)

# Convertit les centres de clusters en un DataFrame avec les colonnes 'Lat' et 'Lon'
center_k = pd.DataFrame(center, columns=["Lat", "Lon"])

# Ajoute une colonne 'size' au DataFrame pour spécifier la taille des marqueurs à utiliser lors de la visualisation
center_k["size"] = 10

In [23]:
# Crée un graphique scatter mapbox avec les données de df_sat_0, en utilisant les colonnes 'Lat' et 'Lon' comme coordonnées et colorant les points en fonction du cluster k-means
fig = px.scatter_mapbox(df_sat_0, lat="Lat", lon="Lon", color='clusterkmeans',size_max=15, zoom=8, width=800, height=800)

# Met à jour le style de la carte Mapbox pour utiliser "carto-positron"
fig.update_layout(mapbox_style="carto-positron")

# Crée un autre graphique scatter mapbox avec les centres de clusters, en utilisant les colonnes 'Lat' et 'Lon' comme coordonnées et spécifiant la taille des marqueurs
fig2 = px.scatter_mapbox(center_k, lat="Lat", lon="Lon", size="size", title="Hotspot des prises en charge de courses Uber")

# Ajoute les marqueurs des centres de clusters au graphique principal
fig.add_trace(fig2.data[0])

# Affiche le graphique
fig.show()


On peut voir avec ce graphique que les hotspot sont :
- les abords de Central Park (cluster jaune)
- le sud de Manhattan (cluster bleu)
- South Williamsburg (cluster orange)
- l'ouest de Brooklyn et South Slope (cluster violet)

### HOT SPOT PAR JOUR DE LA SEMAINE

In [24]:
# Crée une fonction pour obtenir les centres de clusters pour un jour et une heure donnés
def get_centers(day, hour):
    _, center = cluster_day_hour(manhattan_data, day, hour)
    return pd.DataFrame({
        'Day': [day] * 4,
        'Hour': [hour] * 4,
        'Center_lat': center[:, 0],
        'Center_lon': center[:, 1]
    })

# Utilise la méthode apply pour appliquer la fonction à chaque combinaison de jour et d'heure
centers = pd.concat([get_centers(i, j) for i in range(7) for j in range(24)], ignore_index=True)


In [25]:
fig = px.scatter_mapbox(centers, lat="Center_lat", lon="Center_lon",
            animation_frame = 'Day', animation_group = 'Hour', 
            color="Hour", title="Distribution des courses par jour selon l'heure", size_max=15, zoom=8, width=800, height=800)
fig.update_layout(mapbox_style="carto-positron")
fig.show()

Avec cette visualisation on peut voir que les hotspot du graphique précédents sont présents.
Cependant on remarque aussi d'autres zones apparentes :
- L'aéroport de Newark Liberty à l'ouest de Manhattan
- L'aéroport de LaGuardia à l'est de Manhattan